In [3]:
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from scipy.integrate import odeint

### Definition of Lorenz System
x' = σ(y−x) <br>
y' = ρx−y−xz <br>
z' = −βz+xy <br>

In [4]:
# Define constants
rho = 28  # scaled Rayleigh number
sigma = 10  # Prandtl number
beta = 8 / 3  # geometry aspect ratio


# Define lorenz system
def lorenz(x, y, z):
    dx = sigma * (y - x)
    dy = rho * x - y - x * z
    dz = x * y - beta * z
    return np.array([dx, dy, dz])

### Numerical Methods to Solve Lorenz System

### 1. Euler's Method
y<sub>n+1</sub> = y<sub>n</sub> + h*f(x<sub>n</sub>,y<sub>n</sub>)  ,    n= 0,1,...

In [12]:
def eulers_method(initial_values, num_time_pts, h):
    """Solves first order non-linear differential equation systems with Euler's method.
    Args:
        initial_values: initial x,y,z values
        num_time_pts: number of time points to plot
        h: next_value - current_value
    Returns:
        2-D array: trajectory of lorenz attractor
    """
    # trajectory = [[x0,x1,x2,...], [y1,y2,y3],...], [z1,z2,z3,...]]
    trajectory = np.zeros((3, num_time_pts))  # trajectory matrix
    # x, y, z = initial_values[0], initial_values[1], initial_values[2]
    x, y, z = initial_values
    for i in range(0, num_time_pts):
        trajectory[0, i] = x
        trajectory[1, i] = y
        trajectory[2, i] = z

        x_next = x + h * lorenz(x, y, z)[0]
        y_next = y + h * lorenz(x, y, z)[1]
        z_next = z + h * lorenz(x, y, z)[2]
        x, y, z = x_next, y_next, z_next
    return trajectory

### 2. Heun's Method (Modified Euler Method)
y<sub>n+1</sub> = y<sub>n</sub> + (h/2) (f(x<sub>n</sub>, y<sub>n</sub>) + f(x<sub>n</sub> + h, y<sub>n</sub> +  h f(x<sub>n</sub>, y<sub>n</sub>)))


In [15]:
def heuns_method(initial_values, num_time_pts, h):
    """Solves first order non-linear differential equation systems with Heun's method.
    Args:
        initial_values: initial x,y,z values
        num_time_pts: number of time points to plot
        h: next_value - current_value
    Returns:
        2-D array: trajectory of lorenz attractor
    """
    x, y, z = initial_values
    trajectory = np.zeros((3, num_time_pts))
    for i in range(0, num_time_pts):
        trajectory[0, i] = x
        trajectory[1, i] = y
        trajectory[2, i] = z

        # calculate mid points
        x_mid = x + h * lorenz(x, y, z)[0]
        y_mid = y + h * lorenz(x, y, z)[1]
        z_mid = z + h * lorenz(x, y, z)[2]

        # calculate slopes at initial points
        s_0x = lorenz(x, y, z)[0]
        s_0y = lorenz(x, y, z)[1]
        s_0z = lorenz(x, y, z)[2]

        # calculate slopes at midpoints
        s_mx = lorenz(x_mid, y_mid, z_mid)[0]
        s_my = lorenz(x_mid, y_mid, z_mid)[1]
        s_mz = lorenz(x_mid, y_mid, z_mid)[2]

        # update x,y,z points
        x_next = x + (h / 2) * (s_0x + s_mx)
        y_next = y + (h / 2) * (s_0y + s_my)
        z_next = z + (h / 2) * (s_0z + s_mz)

        x, y, z = x_next, y_next, z_next

    return trajectory

### 3. Runge-Kutta Method of Order Four

In [20]:
def simulation(initial_state,method_name):
    x_init, y_init, z_init = initial_state
    fig = go.Figure(
        data=[
            go.Scatter3d(
                x=x_init, y=y_init, z=z_init, mode="lines", marker=dict(size=2)
            )
        ]
    )

    # Customize layout
    fig.update_layout(
        scene=dict(
            aspectmode="cube",
            xaxis=dict(title="X"),
            yaxis=dict(title="Y"),
            zaxis=dict(title="Z"),
        ),
        title=f"Lorenz Attractor({method_name})",
        margin=dict(l=0, r=0, b=0, t=40),
    )
    fig.show()

In [21]:
initial_state = [0, 1, 20]
trajectory_eulers = eulers_method(initial_state, 25000, 0.001)
trajectory_heuns = heuns_method(initial_state, 25000, 0.001)
sim_euler = simulation(trajectory_eulers,"Euler's method")
sim_heuns = simulation(trajectory_heuns,"Heun's method")

Resources
1. https://plotly.com/python/3d-line-plots/
2. https://matplotlib.org/stable/api/_as_gen/matplotlib.axes.Axes.scatter.html#matplotlib.axes.Axes.scatter </br>
For the numerical methods: </br>
3. Goode, S. W., & Annin, S. A. (2014). Differential Equations and Linear Algebra (Pearson New International Edition, Third Edition). Pearson Higher Ed. </br>
For the lorenz system:
4. Hateley, J.C. (2016). THE LORENZ SYSTEM 1 FORMULATION 1 Formulation. <br>
5. Wang, X., & Wang, M. (2008). A hyperchaos generated from Lorenz system. Physica A: Statistical Mechanics and Its Applications, 387(14), 3751–3758. https://doi.org/10.1016/j.physa.2008.02.020